# Seleção de características para aprovação de crédito

In [1]:
import time
import itertools
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import statsmodels.api as sm

from csv import reader
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.compose import ColumnTransformer
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import train_test_split
from sklearn.feature_selection import SelectFromModel
from sklearn.linear_model import Lasso, LogisticRegression
from sklearn.preprocessing import LabelEncoder, OrdinalEncoder, OneHotEncoder, StandardScaler, PolynomialFeatures

In [2]:
# fixar a semente do gerador de números aleatórios
RANDOM_SEED = 42
np.random.seed(RANDOM_SEED)

In [3]:
# mostrar todas as colunas do dataset
pd.set_option('display.max_columns', None)

### 1. Explorando o dataset

In [4]:
# carregando o dataset
df = pd.read_csv("datasets/application_data.csv", sep=",", encoding="latin-1")
df.head(10)

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
0      100002       1         Cash loans           M            N   
1      100003       0         Cash loans           F            N   
2      100004       0    Revolving loans           M            Y   
3      100006       0         Cash loans           F            N   
4      100007       0         Cash loans           M            N   
5      100008       0         Cash loans           M            N   
6      100009       0         Cash loans           F            Y   
7      100010       0         Cash loans           M            Y   
8      100011       0         Cash loans           F            N   
9      100012       0    Revolving loans           M            N   

  FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
0               Y             0          202500.0    406597.5      24700.5   
1               N             0          270000.0   1293502.5      35698.5   
2               Y             0           67500.0    135000.0       6750.0   
3               Y             0          135000.0    312682.5      29686.5   
4               Y             0          121500.0    513000.0      21865.5   
5               Y             0           99000.0    490495.5      27517.5   
6               Y             1          171000.0   1560726.0      41301.0   
7               Y             0          360000.0   1530000.0      42075.0   
8               Y             0          112500.0   1019610.0      33826.5   
9               Y             0          135000.0    405000.0      20250.0   

   AMT_GOODS_PRICE  NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
0         351000.0    Unaccompanied               Working   
1        1129500.0           Family         State servant   
2         135000.0    Unaccompanied               Working   
3         297000.0    Unaccompanied               Working   
4         513000.0    Unaccompanied               Working   
5         454500.0  Spouse, partner         State servant   
6        1395000.0    Unaccompanied  Commercial associate   
7        1530000.0    Unaccompanied         State servant   
8         913500.0         Children             Pensioner   
9         405000.0    Unaccompanied               Working   

             NAME_EDUCATION_TYPE    NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  \
0  Secondary / secondary special  Single / not married  House / apartment   
1               Higher education               Married  House / apartment   
2  Secondary / secondary special  Single / not married  House / apartment   
3  Secondary / secondary special        Civil marriage  House / apartment   
4  Secondary / secondary special  Single / not married  House / apartment   
5  Secondary / secondary special               Married  House / apartment   
6               Higher education               Married  House / apartment   
7               Higher education               Married  House / apartment   
8  Secondary / secondary special               Married  House / apartment   
9  Secondary / secondary special  Single / not married  House / apartment   

   REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  DAYS_REGISTRATION  \
0                    0.018801       -9461           -637            -3648.0   
1                    0.003541      -16765          -1188            -1186.0   
2                    0.010032      -19046           -225            -4260.0   
3                    0.008019      -19005          -3039            -9833.0   
4                    0.028663      -19932          -3038            -4311.0   
5                    0.035792      -16941          -1588            -4970.0   
6                    0.035792      -13778          -3130            -1213.0   
7                    0.003122      -18850           -449            -4597.0   
8                    0.018634      -20099         365243            -7427.0   
9                    0.019689      -14469          -2019           -14437.

In [5]:
df.describe()

SK_ID_CURR         TARGET   CNT_CHILDREN  AMT_INCOME_TOTAL  \
count  307511.000000  307511.000000  307511.000000      3.075110e+05   
mean   278180.518577       0.080729       0.417052      1.687979e+05   
std    102790.175348       0.272419       0.722121      2.371231e+05   
min    100002.000000       0.000000       0.000000      2.565000e+04   
25%    189145.500000       0.000000       0.000000      1.125000e+05   
50%    278202.000000       0.000000       0.000000      1.471500e+05   
75%    367142.500000       0.000000       1.000000      2.025000e+05   
max    456255.000000       1.000000      19.000000      1.170000e+08   

         AMT_CREDIT    AMT_ANNUITY  AMT_GOODS_PRICE  \
count  3.075110e+05  307499.000000     3.072330e+05   
mean   5.990260e+05   27108.573909     5.383962e+05   
std    4.024908e+05   14493.737315     3.694465e+05   
min    4.500000e+04    1615.500000     4.050000e+04   
25%    2.700000e+05   16524.000000     2.385000e+05   
50%    5.135310e+05   24903.000000     4.500000e+05   
75%    8.086500e+05   34596.000000     6.795000e+05   
max    4.050000e+06  258025.500000     4.050000e+06   

       REGION_POPULATION_RELATIVE     DAYS_BIRTH  DAYS_EMPLOYED  \
count               307511.000000  307511.000000  307511.000000   
mean                     0.020868  -16036.995067   63815.045904   
std                      0.013831    4363.988632  141275.766519   
min                      0.000290  -25229.000000  -17912.000000   
25%                      0.010006  -19682.000000   -2760.000000   
50%                      0.018850  -15750.000000   -1213.000000   
75%                      0.028663  -12413.000000    -289.000000   
max                      0.072508   -7489.000000  365243.000000   

       DAYS_REGISTRATION  DAYS_ID_PUBLISH    OWN_CAR_AGE     FLAG_MOBIL  \
count      307511.000000    307511.000000  104582.000000  307511.000000   
mean        -4986.120328     -2994.202373      12.061091       0.999997   
std          3522.886321      1509.450419      11.944812       0.001803   
min        -24672.000000     -7197.000000       0.000000       0.000000   
25%         -7479.500000     -4299.000000       5.000000       1.000000   
50%         -4504.000000     -3254.000000       9.000000       1.000000   
75%         -2010.000000     -1720.000000      15.000000       1.000000   
max             0.000000         0.000000      91.000000       1.000000   

       FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE     FLAG_PHONE  \
count   307511.000000    307511.000000     307511.000000  307511.000000   
mean         0.819889         0.199368          0.998133       0.281066   
std          0.384280         0.399526          0.043164       0.449521   
min          0.000000         0.000000          0.000000       0.000000   
25%          1.000000         0.000000          1.000000       0.000000   
50%          1.000000         0.000000          1.000000       0.000000   
75%          1.000000         0.000000          1.000000       1.000000   
max          1.000000         1.000000          1.000000       1.000000   

          FLAG_EMAIL  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
count  307511.000000    307509.000000         307511.000000   
mean        0.056720         2.152665              2.052463   
std         0.231307         0.910682              0.509034   
min         0.000000         1.000000              1.000000   
25%         0.000000         2.000000              2.000000   
50%         0.000000         2.000000              2.000000   
75%         0.000000         3.000000              2.000000   
max         1.000000        20.000000              3.000000   

       REGION_RATING_CLIENT_W_CITY  HOUR_APPR_PROCESS_START  \
count                307511.000000            307511.000000   
mean                      2.031521                12.063419   
std                       0.502737                 3.265832   
min                       1.000000                 0.000000   
25%                       

In [6]:
df["NAME_CONTRACT_TYPE"].value_counts()

Cash loans         278232
Revolving loans     29279
Name: NAME_CONTRACT_TYPE, dtype: int64

In [7]:
df["CODE_GENDER"].value_counts()

F      202448
M      105059
XNA         4
Name: CODE_GENDER, dtype: int64

In [8]:
df["FLAG_OWN_CAR"].value_counts()

N    202924
Y    104587
Name: FLAG_OWN_CAR, dtype: int64

In [9]:
df["FLAG_OWN_REALTY"].value_counts()

Y    213312
N     94199
Name: FLAG_OWN_REALTY, dtype: int64

### 2. Limpando o dataset

#### 2.1 Substituindo valores NaN

In [10]:
columns_with_null_values = []
    
for column in df:
    if df[column].isnull().any():
        columns_with_null_values.append(column)

len(columns_with_null_values)

67

In [11]:
df[columns_with_null_values].isnull().sum().sort_values(ascending = False)

COMMONAREA_MEDI             214865
COMMONAREA_AVG              214865
COMMONAREA_MODE             214865
NONLIVINGAPARTMENTS_AVG     213514
NONLIVINGAPARTMENTS_MODE    213514
                             ...  
EXT_SOURCE_2                   660
AMT_GOODS_PRICE                278
AMT_ANNUITY                     12
CNT_FAM_MEMBERS                  2
DAYS_LAST_PHONE_CHANGE           1
Length: 67, dtype: int64

In [12]:
drop_columns = []
columns_to_analyze = []

for column in columns_with_null_values:
    if df[column].isnull().sum() > len(df)/2:
        drop_columns.append(column)
    else:
        columns_to_analyze.append(column)
        
len(drop_columns)

41

In [13]:
total_before_drop = len(df.columns)

df = df.drop(columns = drop_columns)
total_after_drop = len(df.columns)

print("{0} - {1} = {2}".format(total_before_drop, len(drop_columns), total_after_drop))

122 - 41 = 81


In [14]:
df[columns_to_analyze].isnull().sum().sort_values(ascending = False)

FLOORSMAX_MEDI                  153020
FLOORSMAX_AVG                   153020
FLOORSMAX_MODE                  153020
YEARS_BEGINEXPLUATATION_AVG     150007
YEARS_BEGINEXPLUATATION_MODE    150007
YEARS_BEGINEXPLUATATION_MEDI    150007
TOTALAREA_MODE                  148431
EMERGENCYSTATE_MODE             145755
OCCUPATION_TYPE                  96391
EXT_SOURCE_3                     60965
AMT_REQ_CREDIT_BUREAU_QRT        41519
AMT_REQ_CREDIT_BUREAU_YEAR       41519
AMT_REQ_CREDIT_BUREAU_HOUR       41519
AMT_REQ_CREDIT_BUREAU_DAY        41519
AMT_REQ_CREDIT_BUREAU_WEEK       41519
AMT_REQ_CREDIT_BUREAU_MON        41519
NAME_TYPE_SUITE                   1292
OBS_30_CNT_SOCIAL_CIRCLE          1021
DEF_30_CNT_SOCIAL_CIRCLE          1021
OBS_60_CNT_SOCIAL_CIRCLE          1021
DEF_60_CNT_SOCIAL_CIRCLE          1021
EXT_SOURCE_2                       660
AMT_GOODS_PRICE                    278
AMT_ANNUITY                         12
CNT_FAM_MEMBERS                      2
DAYS_LAST_PHONE_CHANGE   

In [15]:
df[columns_to_analyze].describe()

AMT_ANNUITY  AMT_GOODS_PRICE  CNT_FAM_MEMBERS  EXT_SOURCE_2  \
count  307499.000000     3.072330e+05    307509.000000  3.068510e+05   
mean    27108.573909     5.383962e+05         2.152665  5.143927e-01   
std     14493.737315     3.694465e+05         0.910682  1.910602e-01   
min      1615.500000     4.050000e+04         1.000000  8.173617e-08   
25%     16524.000000     2.385000e+05         2.000000  3.924574e-01   
50%     24903.000000     4.500000e+05         2.000000  5.659614e-01   
75%     34596.000000     6.795000e+05         3.000000  6.636171e-01   
max    258025.500000     4.050000e+06        20.000000  8.549997e-01   

        EXT_SOURCE_3  YEARS_BEGINEXPLUATATION_AVG  FLOORSMAX_AVG  \
count  246546.000000                157504.000000  154491.000000   
mean        0.510853                     0.977735       0.226282   
std         0.194844                     0.059223       0.144641   
min         0.000527                     0.000000       0.000000   
25%         0.370650                     0.976700       0.166700   
50%         0.535276                     0.981600       0.166700   
75%         0.669057                     0.986600       0.333300   
max         0.896010                     1.000000       1.000000   

       YEARS_BEGINEXPLUATATION_MODE  FLOORSMAX_MODE  \
count                 157504.000000   154491.000000   
mean                       0.977065        0.222315   
std                        0.064575        0.143709   
min                        0.000000        0.000000   
25%                        0.976700        0.166700   
50%                        0.981600        0.166700   
75%                        0.986600        0.333300   
max                        1.000000        1.000000   

       YEARS_BEGINEXPLUATATION_MEDI  FLOORSMAX_MEDI  TOTALAREA_MODE  \
count                 157504.000000   154491.000000   159080.000000   
mean                       0.977752        0.225897        0.102547   
std                        0.059897        0.145067        0.107462   
min                        0.000000        0.000000        0.000000   
25%                        0.976700        0.166700        0.041200   
50%                        0.981600        0.166700        0.068800   
75%                        0.986600        0.333300        0.127600   
max                        1.000000        1.000000        1.000000   

       OBS_30_CNT_SOCIAL_CIRCLE  DEF_30_CNT_SOCIAL_CIRCLE  \
count             306490.000000             306490.000000   
mean                   1.422245                  0.143421   
std                    2.400989                  0.446698   
min                    0.000000                  0.000000   
25%                    0.000000                  0.000000   
50%                    0.000000                  0.000000   
75%                    2.000000                  0.000000   
max                  348.000000                 34.000000   

       OBS_60_CNT_SOCIAL_CIRCLE  DEF_60_CNT_SOCIAL_CIRCLE  \
count             306490.000000             306490.000000   
mean                   1.405292                  0.100049   
std                    2.379803                  0.362291   
min                    0.000000                  0.000000   
25%                    0.000000                  0.000000   
50%                    0.000000                  0.000000   
75%                    2.000000                  0.000000   
max                  344.000000                 24.000000   

       DAYS_LAST_PHONE_CHANGE  AMT_REQ_CREDIT_BUREAU_HOUR  \
count           307510.000000               265992.000000   
mean              -962.858788                    0.006402   
std                826.808487                    0.083849   
min              -4292.000000                    0.000000   
25%              -1570.000000                    0.000000   
50%               -757.000000                    0.000000   
75%               -274.000000                    0.000000   
max                  0.

In [16]:
# Listas com colunas de moda e mediana
mode_list = []
median_list = []

for column in columns_to_analyze:
    suffix = column[-4:]
    if suffix == "MODE":
        mode_list.append(column)
    elif suffix == "MEDI":
        median_list.append(column)

In [17]:
# MODA
mode_list.remove('EMERGENCYSTATE_MODE')

for column in mode_list:
    df[column] = df[column].fillna(df[column].mode()[0])

    columns_to_analyze.remove(column)

In [18]:
# MEDIANA
for column in median_list:
    df[column] = df[column].fillna(df[column].median())

    columns_to_analyze.remove(column)

In [19]:
# Lista com colunas médias
avg_list = []

for column in columns_to_analyze:
    suffix = column[-3:]
    prefix = column[:3]
    if suffix == "AVG" or prefix == "AMT" or prefix == "EXT" or df[column].isnull().sum() < 1050:
        avg_list.append(column)        

In [20]:
# MÉDIA
for column in avg_list:
    df[column] = df[column].fillna(df[column].mean())
    columns_to_analyze.remove(column)

In [21]:
df[columns_to_analyze].isnull().sum().sort_values(ascending = False)

EMERGENCYSTATE_MODE    145755
OCCUPATION_TYPE         96391
NAME_TYPE_SUITE          1292
dtype: int64

In [22]:
df['NAME_TYPE_SUITE'] = df['NAME_TYPE_SUITE'].fillna('Unaccompanied')
df['EMERGENCYSTATE_MODE'] = df['EMERGENCYSTATE_MODE'].fillna('Undefined')
df['OCCUPATION_TYPE'] = df['OCCUPATION_TYPE'].fillna('Other')

In [23]:
df.isnull().any()

SK_ID_CURR                    False
TARGET                        False
NAME_CONTRACT_TYPE            False
CODE_GENDER                   False
FLAG_OWN_CAR                  False
                              ...  
AMT_REQ_CREDIT_BUREAU_DAY     False
AMT_REQ_CREDIT_BUREAU_WEEK    False
AMT_REQ_CREDIT_BUREAU_MON     False
AMT_REQ_CREDIT_BUREAU_QRT     False
AMT_REQ_CREDIT_BUREAU_YEAR    False
Length: 81, dtype: bool

#### 2.2 Removendo colunas irrelevantes

In [24]:
remove_data = []

for column in df.columns:
    if column[:3] == 'EXT':
        remove_data.append(column)
    elif column[:8] == 'FLAG_DOC':
        remove_data.append(column)
        
len(remove_data)

22

In [25]:
df = df.drop(columns=remove_data, axis=1)

#### 2.3 Convertendo categóricas

In [26]:
df = pd.get_dummies(df)
df.head()

SK_ID_CURR  TARGET  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
0      100002       1             0          202500.0    406597.5   
1      100003       0             0          270000.0   1293502.5   
2      100004       0             0           67500.0    135000.0   
3      100006       0             0          135000.0    312682.5   
4      100007       0             0          121500.0    513000.0   

   AMT_ANNUITY  AMT_GOODS_PRICE  REGION_POPULATION_RELATIVE  DAYS_BIRTH  \
0      24700.5         351000.0                    0.018801       -9461   
1      35698.5        1129500.0                    0.003541      -16765   
2       6750.0         135000.0                    0.010032      -19046   
3      29686.5         297000.0                    0.008019      -19005   
4      21865.5         513000.0                    0.028663      -19932   

   DAYS_EMPLOYED  DAYS_REGISTRATION  DAYS_ID_PUBLISH  FLAG_MOBIL  \
0           -637            -3648.0            -2120           1   
1          -1188            -1186.0             -291           1   
2           -225            -4260.0            -2531           1   
3          -3039            -9833.0            -2437           1   
4          -3038            -4311.0            -3458           1   

   FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  FLAG_EMAIL  \
0               1                0                 1           1           0   
1               1                0                 1           1           0   
2               1                1                 1           1           0   
3               1                0                 1           0           0   
4               1                0                 1           0           0   

   CNT_FAM_MEMBERS  REGION_RATING_CLIENT  REGION_RATING_CLIENT_W_CITY  \
0              1.0                     2                            2   
1              2.0                     1                            1   
2              1.0                     2                            2   
3              2.0                     2                            2   
4              1.0                     2                            2   

   HOUR_APPR_PROCESS_START  REG_REGION_NOT_LIVE_REGION  \
0                       10                           0   
1                       11                           0   
2                        9                           0   
3                       17                           0   
4                       11                           0   

   REG_REGION_NOT_WORK_REGION  LIVE_REGION_NOT_WORK_REGION  \
0                           0                            0   
1                           0                            0   
2                           0                            0   
3                           0                            0   
4                           0                            0   

   REG_CITY_NOT_LIVE_CITY  REG_CITY_NOT_WORK_CITY  LIVE_CITY_NOT_WORK_CITY  \
0                       0                       0                        0   
1                       0                       0                        0   
2                       0                       0                        0   
3                       0                       0                        0   
4                       0                       1                        1   

   YEARS_BEGINEXPLUATATION_AVG  FLOORSMAX_AVG  YEARS_BEGINEXPLUATATION_MODE  \
0                     0.972200       0.083300                        0.9722   
1                     0.985100       0.291700                        0.9851   
2                     0.977735       0.226282                        0.9871   
3                     0.977735       0.226282                        0.9871   
4                     0.977735       0.226282                        0.9871   

   FLOORSMAX_MODE  YEARS_BEGINEXPLUATATION_MEDI  FLOORSMAX_MEDI  \
0          0.0833                        0.9722          0.0833   
1       

### 3. Dividindo conjuntos de teste e treinamento

In [27]:
train_set, test_set = train_test_split(df, test_size=0.2, random_state=RANDOM_SEED)
print("{} train + {} test".format(len(train_set), len(test_set)))

246008 train + 61503 test


### 4. Correlação entre as features

In [28]:
def correlation_color(value):
    if value == 1:
        color = 'gold'
    elif abs(value) > 0.75:
        color = 'royalblue'
    elif value < 0:
        color = 'red'
    else:
        color = 'green'
    return 'color: %s' % color

In [29]:
pd.set_option('display.max_rows', None)
correlation = train_set.corr().style.applymap(correlation_color)
correlation

### 4. Separando a variável dependente: TARGET

In [30]:
x_train = train_set.drop(columns=["TARGET"])
y_train = train_set["TARGET"]
x_test = test_set.drop(columns=["TARGET"])
y_test = test_set["TARGET"]

### 5. Ajustando variáveis categóricas

In [31]:
categoricas = list(x_train.select_dtypes('object').columns)
categoricas

[]

In [32]:
#One Hot Encoding
encoder = OneHotEncoder(categories="auto")

cat_1hot = encoder.fit_transform(x_train[categoricas])
cat_1hot.toarray()

array([], shape=(246008, 0), dtype=float64)

In [33]:
x_train_num = x_train.drop(columns=x_train[categoricas], axis=1)
x_test_num = x_test.drop(columns=x_test[categoricas], axis=1)
x_train_num.head()

SK_ID_CURR  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
123473      243191             0          171000.0    555273.0      16366.5   
10118       111778             1          157500.0    198085.5      23638.5   
64716       175057             0          135000.0    776304.0      25173.0   
234940      372147             1          164133.0    900000.0      36787.5   
236051      373412             0          225000.0    533668.5      21294.0   

        AMT_GOODS_PRICE  REGION_POPULATION_RELATIVE  DAYS_BIRTH  \
123473         463500.0                    0.035792      -23349   
10118          171000.0                    0.010032      -10921   
64716          648000.0                    0.035792      -23213   
234940         900000.0                    0.030755      -10703   
236051         477000.0                    0.025164      -15798   

        DAYS_EMPLOYED  DAYS_REGISTRATION  DAYS_ID_PUBLISH  FLAG_MOBIL  \
123473         365243            -3595.0            -4408           1   
10118            -117            -4281.0            -3399           1   
64716           -2157            -5680.0            -5009           1   
234940          -2530            -2618.0            -2751           1   
236051          -3520            -8006.0            -5001           1   

        FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
123473               0                0                 1           0   
10118                1                1                 1           1   
64716                1                0                 1           0   
234940               1                1                 1           1   
236051               1                0                 1           0   

        FLAG_EMAIL  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
123473           0              1.0                     2   
10118            0              3.0                     2   
64716            0              2.0                     2   
234940           0              3.0                     2   
236051           0              2.0                     2   

        REGION_RATING_CLIENT_W_CITY  HOUR_APPR_PROCESS_START  \
123473                            2                        9   
10118                             2                        7   
64716                             2                       13   
234940                            2                       10   
236051                            2                       12   

        REG_REGION_NOT_LIVE_REGION  REG_REGION_NOT_WORK_REGION  \
123473                           0                           0   
10118                            0                           0   
64716                            0                           0   
234940                           0                           0   
236051                           0                           0   

        LIVE_REGION_NOT_WORK_REGION  REG_CITY_NOT_LIVE_CITY  \
123473                            0                       0   
10118                             0                       0   
64716                             0                       0   
234940                            0                       0   
236051                            0                       0   

        REG_CITY_NOT_WORK_CITY  LIVE_CITY_NOT_WORK_CITY  \
123473                       0                        0   
10118                        0                        0   
64716                        0                        0   
234940                       1                        1   
236051                       0                        0   

        YEARS_BEGINEXPLUATATION_AVG  FLOORSMAX_AVG  \
123473                     0.977735       0.226282   
10118                      0.974200       0.166700   
64716                      0.977735       0.226282   
234940                     0.984100       0.333300   
236051                     0.977735       0.226282   

        YEARS_BEGINEXPLUATATION_MODE  FLOORS

In [34]:
num_pipeline = Pipeline(
    [
        ("imputer", SimpleImputer(strategy="median")),
        ("std_scaler", StandardScaler()),
    ]
)

x_train_num_tr = num_pipeline.fit_transform(x_train_num)
x_test_num_tr = num_pipeline.fit_transform(x_test_num)

x_train_num_tr

array([[-0.34107509, -0.57756555,  0.02430965, ..., -1.03668764,
         1.05271092, -0.08782518],
       [-1.61900026,  0.81004476, -0.10484026, ...,  0.96461071,
        -0.9499284 , -0.08782518],
       [-1.00364389, -0.57756555, -0.32009011, ..., -1.03668764,
         1.05271092, -0.08782518],
       ...,
       [-0.24553192, -0.57756555,  2.69340773, ...,  0.96461071,
        -0.9499284 , -0.08782518],
       [-0.07769685,  0.81004476,  0.11040958, ...,  0.96461071,
        -0.9499284 , -0.08782518],
       [-0.35855001, -0.57756555, -0.10484026, ..., -1.03668764,
         1.05271092, -0.08782518]])

In [35]:
#para juntar a numerica com a categorica
num_attribs_train = list(x_train_num)
num_attribs_test = list(x_test_num)

full_pipeline = ColumnTransformer(
    [
        ("num", num_pipeline, num_attribs_train),
        ("cat", OneHotEncoder(sparse=False), categoricas),
    ]
)

full_pipeline_test = ColumnTransformer(
    [
        ("num", num_pipeline, num_attribs_test),
        ("cat", OneHotEncoder(sparse=False), categoricas),
    ]
)

# x_train_prepared = full_pipeline.fit_transform(x_train)
# x_test_prepared = full_pipeline_test.fit_transform(x_test)

In [ ]:
# x_train.to_csv("datasets/train_dataset.csv", index=True)

### 5. Lasso Regression

In [ ]:
def experiment(msg, pipeline, X_train, y_train, X_test, y_test):
    pipeline.fit(X_train, y_train)
    
    model = pipeline.named_steps['lin_reg']
    print('{}: \nintercept = {},\ncoefs = {}'.format(msg, model.intercept_, model.coef_))
    
    y_pred = pipeline.predict(X_test)
    RMSE = np.sqrt(mean_squared_error(y_pred, y_test))
    print('RMSE: {}'.format(RMSE))
    print()
    
alpha = 1e-3

# Test o fit da regularização lasso.
reg_lasso = Pipeline([
        ("std_scaler", StandardScaler()), 
        ("lin_reg", Lasso(alpha=alpha))
    ])
experiment('Regularização Lasso', reg_lasso, x_train, y_train, x_test, y_test)

### 6. Forward Stepwise Selection

In [39]:
x_train_short = x_train[0:1000]
x_test_short = x_test[0:1000]
y_train_short = y_train[0:1000]
y_test_short = y_test[0:1000]

In [ ]:
def processSubset(feature_set):
    # Fit model on feature_set and calculate RSS
    model = sm.OLS(y_train_short,x_train_short[list(feature_set)])
    regr = model.fit()
    RSS = ((regr.predict(x_test_short[list(feature_set)]) - y_test_short) ** 2).sum()
    return {"model":regr, "RSS":RSS}

In [ ]:
def forward(predictors):

    # Pull out predictors we still need to process
    remaining_predictors = [p for p in x_train_short.columns if p not in predictors]
    
    tic = time.time()
    
    results = []
    
    for p in remaining_predictors:
        results.append(processSubset(predictors+[p]))
    
    # Wrap everything up in a nice dataframe
    models = pd.DataFrame(results)
    
    # Choose the model with the highest RSS
    best_model = models.loc[models['RSS'].argmin()]
    
    toc = time.time()
    print("Processed ", models.shape[0], "models on", len(predictors)+1, "predictors in", (toc-tic), "seconds.")
    
    # Return the best model, along with some other useful information about the model
    return best_model

In [ ]:
models_fwd = pd.DataFrame(columns=["RSS", "model"])

tic = time.time()
predictors = []

for i in range(1,len(x_train_short.columns)+1):    
    models_fwd.loc[i] = forward(predictors)
    predictors = models_fwd.loc[i]["model"].model.exog_names

toc = time.time()
print("Total elapsed time:", (toc-tic), "seconds.")

In [ ]:
print(models_fwd.loc[10, "model"].summary())

### 7. Backward Elimination

In [ ]:
def backward(predictors):
    
    tic = time.time()
    
    results = []
    
    for combo in itertools.combinations(predictors, len(predictors)-1):
        results.append(processSubset(combo))
    
    # Wrap everything up in a nice dataframe
    models = pd.DataFrame(results)
    
    # Choose the model with the highest RSS
    best_model = models.loc[models['RSS'].argmin()]
    
    toc = time.time()
    print("Processed ", models.shape[0], "models on", len(predictors)-1, "predictors in", (toc-tic), "seconds.")
    
    # Return the best model, along with some other useful information about the model
    return best_model

In [ ]:
models_bwd = pd.DataFrame(columns=["RSS", "model"], index = range(1,len(x_train_short.columns)))

tic = time.time()
predictors = x_train_short.columns

while(len(predictors) > 1):  
    models_bwd.loc[len(predictors)-1] = backward(predictors)
    predictors = models_bwd.loc[len(predictors)-1]["model"].model.exog_names

toc = time.time()
print("Total elapsed time:", (toc-tic), "seconds.")

In [ ]:
print(models_bwd.loc[10, "model"].summary())

In [ ]:
print("-----------------")
print("Foward Selection:")
print("-----------------")
print(models_fwd.loc[10, "model"].params)

In [ ]:
print("-------------------")
print("Backward Selection:")
print("-------------------")
print(models_bwd.loc[10, "model"].params)

In [ ]:
x_train.head(25)

In [37]:
import numpy as np
import pandas as pd
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score as acc
from mlxtend.feature_selection import SequentialFeatureSelector as sfs

In [40]:
# Build RF classifier to use in feature selection
clf = RandomForestClassifier(n_estimators=100, n_jobs=-1)

# Build step forward feature selection
sfs1 = sfs(clf,
           k_features=5,
           forward=True,
           floating=False,
           verbose=2,
           scoring='accuracy',
           cv=5)

# Perform SFFS
sfs1 = sfs1.fit(x_train_short, y_train_short)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    2.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 173 out of 173 | elapsed:  7.4min finished

[2020-11-27 01:41:04] Features: 1/5 -- score: 0.915[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    2.3s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 172 out of 172 | elapsed:  7.6min finished

[2020-11-27 01:48:38] Features: 2/5 -- score: 0.916[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    3.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done 171 out of 171 | elapsed:  8.3min finished

[2020-11-27 01:56:58] Features: 3/5 -- score: 0.916[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    2.5s remaining

In [41]:
# Which features?
feat_cols = list(sfs1.k_feature_idx_)
print(feat_cols)

[11, 14, 21, 27, 50]


11 -> flag_mobil
14 -> flag_cont_mobile
21 -> REG_REGION_NOT_LIVE_REGION
27 -> YEARS_BEGINEXPLUATATION_AVG
50 -> FLAG_OWN_CAR_N	

In [49]:
# Build full model with selected features
feat_cols = ['FLAG_MOBIL', 'FLAG_CONT_MOBILE', 'REG_REGION_NOT_LIVE_REGION', 'YEARS_BEGINEXPLUATATION_AVG', 'FLAG_OWN_CAR_N']
clf = RandomForestClassifier(n_estimators=1000, random_state=42, max_depth=4)
clf.fit(x_train[feat_cols], y_train)

y_train_pred = clf.predict(x_train[feat_cols])
print('Training accuracy on selected features: %.3f' % acc(y_train, y_train_pred))

y_test_pred = clf.predict(x_test[feat_cols])
print('Testing accuracy on selected features: %.3f' % acc(y_test, y_test_pred))

Training accuracy on selected features: 0.919
Testing accuracy on selected features: 0.920


In [50]:
# Build full model on ALL features, for comparison
clf = RandomForestClassifier(n_estimators=1000, random_state=42, max_depth=4)
clf.fit(x_train, y_train)

y_train_pred = clf.predict(x_train)
print('Training accuracy on all features: %.3f' % acc(y_train, y_train_pred))

y_test_pred = clf.predict(x_test)
print('Testing accuracy on all features: %.3f' % acc(y_test, y_test_pred))

Training accuracy on all features: 0.919
Testing accuracy on all features: 0.920


In [56]:
# Build RF classifier to use in feature selection
clf = RandomForestClassifier(n_estimators=100, n_jobs=-1)

# Build step backward feature selection
sbs = sfs(clf,
           k_features=5,
           forward=False,
           floating=False,
           verbose=2,
           scoring='accuracy',
           cv=5)

# Perform SBS
sbs = sbs.fit(x_train_short, y_train_short)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    2.3s remaining:    0.0s

STOPPING EARLY DUE TO KEYBOARD INTERRUPT...

In [57]:
# Which features?
feat_cols = list(sbs.k_feature_idx_)
print(feat_cols)

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172]


In [ ]:
# Build full model with selected features
feat_cols = []
clf = RandomForestClassifier(n_estimators=1000, random_state=42, max_depth=4)
clf.fit(x_train[feat_cols], y_train)

y_train_pred = clf.predict(x_train[feat_cols])
print('Training accuracy on selected features: %.3f' % acc(y_train, y_train_pred))

y_test_pred = clf.predict(x_test[feat_cols])
print('Testing accuracy on selected features: %.3f' % acc(y_test, y_test_pred))